---
# **Project** : **Hands KeyPoints Detection by capturing video from webcam**
---
### ---> **Sahil Kumar 777**

This project capture the video using webcam and then performs hands detection and hands key points detection. It finally provides the recognition video of hand landmarks of the detected hands.

**Objective :-**
* Capture webcam video on Google Colab
* Operates on video data to detect hands Landmarks.

**Modules Used :-**
* OpenCV-Python
* Mediapipe

## Installing Libraries

In [ ]:
# Installing inportant libraries

!pip install opencv-python
!pip install mediapipe
!pip install tensorflow

## Access webcam to Record and Save Video.


In [ ]:
# Function to access webcam then record & save video

from IPython.display import display, Javascript
from google.colab.output import eval_js
from base64 import b64decode

def take_video(filename='myVideo.mp4', quality=0.8):
  js = Javascript('''

    async function takeVideo(quality) {
      const div = document.createElement('div');
      const startButton = document.createElement('button');
      startButton.textContent = 'Start';
      div.appendChild(startButton);

      const stopButton = document.createElement('button');
      stopButton.textContent = 'Stop';
      div.appendChild(stopButton);

      const a = document.createElement('a');

      const video = document.createElement('video');
      video.style.display = 'block';

      document.body.appendChild(div);
      div.appendChild(video);
      let blob;

      // Resize the output to fit the video element.
      google.colab.output.setIframeHeight(document.documentElement.scrollHeight, true);

      let mediaRecorder;
      let recordedChunks = [];

      // Access webcam
      navigator.mediaDevices.getUserMedia({ video: {video:{faceingmode : 'user'}}, audio: false })
        .then(stream => {
          video.srcObject = stream;
          video.play();

          // Initialize MediaRecorder
          mediaRecorder = new MediaRecorder(stream);

          // Collect data chunks
          mediaRecorder.ondataavailable = event => {
            if (event.data.size > 0) recordedChunks.push(event.data);
          };

          // Save video when recording stops
          mediaRecorder.onstop = () => {
            blob = new Blob(recordedChunks, { type: 'video/webm' });

            const url = URL.createObjectURL(blob);

            stream.getVideoTracks()[0].stop();
            // Create a download link
            //const a = document.createElement('a');
            //a.href = url;
            a.textContent = 'Download Link';
            //a.download = 'recorded-video.webm';
            div.appendChild(a);
            //a.click();
            //document.body.removeChild(a);
            video.srcObject = null;
            video.src = url;
            video.controls=true;
            video.play();
            // Reset chunks
            recordedChunks = [];

          };
        })
        .catch(error => console.error('Error accessing webcam:', error));

      // Start recording
      startButton.addEventListener('click', () => {
        mediaRecorder.start();
        startButton.disabled = true;
        stopButton.disabled = false;
      });

      // Stop recording
      stopButton.addEventListener('click', () => {
        mediaRecorder.stop();
        //startButton.disabled = false;
        stopButton.disabled = true;
      });
      await new Promise((resolve)=>a.onclick = resolve);


      return new Promise((resolve, reject) => {
    const reader = new FileReader();
    reader.onload = () => resolve(reader.result); // Base64 string
    reader.onerror = () => reject(reader.error);
    reader.readAsDataURL(blob); // Reads the Blob as a Base64-encoded string
  });
    }
    ''')
  display(js)
  data = eval_js('takeVideo({})'.format(quality))
  binary = b64decode(data.split(',')[1])
  with open(filename, 'wb') as f:
    f.write(binary)
  return filename


In [ ]:
filename = take_video()
print('Saved to {}'.format(filename))

<IPython.core.display.Javascript object>

Saved to myVideo.mp4


## Initialize MediaPipe

In [ ]:
# Importing important libraries
import cv2
import numpy as np
# import tensorflow as tf
import mediapipe as mp
#from tensorflow.keras.models import load_model

# Initialize mediapipe
mpHands = mp.solutions.hands
hands = mpHands.Hands(static_image_mode=False, max_num_hands=1, model_complexity=1, min_detection_confidence=0.7, min_tracking_confidence=0.5)
mpDraw = mp.solutions.drawing_utils

## Initialize Tensorflow

In [ ]:
# from tensorflow.keras.models import load_model
# # Load the gesture recognizer model
# model = load_model('mp_hand_gesture')
# # Load class names
# f = open('gesture.names', 'r')
# classNames = f.read().split('\n')
# f.close()
# print(classNames)

## Detect hand keypoints.
* Drawing detected hand_keypoints
* Saving frames into video


In [ ]:
# Initialize the webcam for Hand Gesture Recognition Python project
cap = cv2.VideoCapture('myVideo.mp4')

# Define the codec and create a VideoWriter object
fourcc = cv2.VideoWriter_fourcc(*'VP80')  # You can use other codecs like 'mp4v' for .mp4 files
fps = 30  # Frames per second


i=0
while True:
  # Read each frame from the webcam
  success, frame = cap.read()
  if not success:
    if i == 0 :
      print("Failed to read from video")
      # Exit
      break
    else :
      print("Hand tracking Video Saved")
      # Exit
      break

  height , width, layers = frame.shape

  if i == 0:
    video_writer = cv2.VideoWriter('lmVideo.webm', fourcc, fps, (width, height))

  # print(i)

  frame = cv2.flip(frame, 1)
  framergb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
  # mpimage = mp.Image(image_format=mp.ImageFormat(1), data=framergb)

  result = hands.process(framergb)
  #className = ''

  # post process the result
  if result.multi_hand_landmarks:
    landmarks = []
    for handslms in result.multi_hand_landmarks:
        for lm in handslms.landmark:
            # print(id, lm)
            lmx = int(lm.x * height)
            lmy = int(lm.y * width)
            landmarks.append([lmx, lmy])
        # Drawing landmarks on frames
        mpDraw.draw_landmarks(frame, handslms, mpHands.HAND_CONNECTIONS)

  video_writer.write(frame)
  i=i+1

# release the webcam and destroy all active windows
video_writer.release()
cap.release()
# cv2.destroyAllWindows() # only required when working in jupyter notebook

Hand tracking Video Saved


## Playing Generated Video

In [ ]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('lmVideo.webm','rb').read()
data_url = "data:video/webm;base64," + b64encode(mp4).decode()

HTML("""
  <video src="%s" type="video/webm" width="640" height="480" controls autoplay>

  </video>
"""  % data_url)

## Recognize hand gestures.

In [ ]:
# # Predict gesture in Hand Gesture Recognition project
# prediction = model.predict([landmarks])
# print(prediction)
# classID = np.argmax(prediction)
# className = classNames[classID]
# # show the prediction on the frame
# cv2.putText(frame, className, (10, 50), cv2.FONT_HERSHEY_SIMPLEX,1, (0,0,255), 2, cv2.LINE_AA)